In [3]:
!pip install gymnasium[atari] stable-baselines3[extra] ale-py

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 119.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 965.4/965.4 kB 87.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.5/5.5 MB 140.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 766.7/766.7 MB 39.6 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 81.8 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 134.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 170.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 111.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 42.8 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 51.9 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 57.6 MB/s eta 0:00:00:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 53.8 MB/s eta 

In [4]:
!pip install ale_py

In [5]:
!pip install wandb
import wandb
wandb.login()

True

In [8]:
!pip install MoviePy

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 29.5/29.5 MB 140.3 MB/s eta 0:00:0000:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.4/4.4 MB 131.8 MB/s eta 0:00:00
  Attempting uninstall: pillow
    Found existing installation: pillow 11.1.0
    Uninstalling pillow-11.1.0:
      Successfully uninstalled pillow-11.1.0


In [11]:
import gymnasium as gym
import ale_py
gym.register_envs(ale_py)
from stable_baselines3 import DQN
from stable_baselines3.common.atari_wrappers import AtariWrapper
from stable_baselines3.common.vec_env import DummyVecEnv, VecVideoRecorder
from stable_baselines3.common.evaluation import evaluate_policy
from stable_baselines3.common.monitor import Monitor
import numpy as np
from gymnasium import RewardWrapper
from wandb.integration.sb3 import WandbCallback

# config for wandb
config = {
    "total_timesteps": 1000000,
    "env_name": "Riverraid-v5",
}
run = wandb.init(
    project="RiverraidDQN",
    config=config,
    sync_tensorboard=True,  # auto-upload sb3's tensorboard metrics
    monitor_gym=True,  # auto-upload the videos of agents playing the game
    save_code=False,  # optional
)

# custom reward wrapper for better results
class RiverraidRewardWrapper(RewardWrapper):
    def __init__(self, env):
        super().__init__(env)
        self.prev_fuel = None
        self.prev_lives = None

    def reset(self, **kwargs):
        obs, info = self.env.reset(**kwargs)
        self.prev_fuel = info.get("fuel", 100)
        self.prev_lives = info.get("lives", 3)
        return obs, info

    def reward(self, reward):
        # Base reward from environment
        shaped_reward = reward

        # Add small time-based survival reward
        shaped_reward += 0.1

        # Penalize if fuel is very low (simulate danger)
        current_fuel = self.env.unwrapped.ale.getRAM()[65]  # RAM address for fuel
        if current_fuel < 20:
            shaped_reward -= 0.5

        # Bonus for fuel collection (fuel increases)
        if self.prev_fuel is not None and current_fuel > self.prev_fuel:
            shaped_reward += 1.0

        self.prev_fuel = current_fuel

        # Penalize for life loss
        current_lives = self.env.unwrapped.ale.lives()
        if self.prev_lives is not None and current_lives < self.prev_lives:
            shaped_reward -= 5.0

        self.prev_lives = current_lives

        # Clip final shaped reward
        return np.clip(shaped_reward, -1, 1)


# Create and wrap the Riverraid environment
def make_env():
    env = gym.make("ALE/Riverraid-v5", render_mode="rgb_array")
    env = Monitor(env)
    env = RiverraidRewardWrapper(env)
    env = AtariWrapper(env)
    return env

env = DummyVecEnv([make_env])
env = VecVideoRecorder(
    env,
    f"videos/{run.id}",
    record_video_trigger=lambda x: x % 50000 == 0,
    video_length=400,
)

# Define and train the DQN model
model = DQN("CnnPolicy", env, verbose=1, buffer_size=100000, learning_starts=10000,
            batch_size=32, gamma=0.99, train_freq=4, target_update_interval=1000, tensorboard_log=f"runs/{run.id}")

# model.learn(total_timesteps=100000)

model.learn(
    total_timesteps=config["total_timesteps"],
    callback=WandbCallback(
        gradient_save_freq=100,
        model_save_path=f"models/{run.id}",
        verbose=2,
    ),
)
run.finish()

# Save the model
model.save("dqn_riverraid")

# Evaluate the trained agent
mean_reward, std_reward = evaluate_policy(model, env, n_eval_episodes=10)
print(f"Mean reward: {mean_reward} +/- {std_reward}")

wandb: WARNING When using several event log directories, please call `wandb.tensorboard.patch(root_logdir="...")` before `wandb.init`


Using cuda device
Wrapping the env in a VecTransposeImage.
Logging to runs/xk82qzec/DQN_1
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 471      |
|    ep_rew_mean      | 960      |
|    exploration_rate | 0.999    |
| time/               |          |
|    episodes         | 4        |
|    fps              | 249      |
|    time_elapsed     | 0        |
|    total_timesteps  | 102      |
----------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 456      |
|    ep_rew_mean      | 840      |
|    exploration_rate | 0.998    |
| time/               |          |
|    episodes         | 8        |
|    fps              | 258      |
|    time_elapsed     | 0        |
|    total_timesteps  | 194      |
----------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 405      |
|    ep_rew_mean      | 713      |


MoviePy - Done !
MoviePy - video ready /home/ec2-user/SageMaker/videos/xk82qzec/rl-video-step-0-to-step-400.mp4
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 434      |
|    ep_rew_mean      | 806      |
|    exploration_rate | 0.996    |
| time/               |          |
|    episodes         | 20       |
|    fps              | 242      |
|    time_elapsed     | 1        |
|    total_timesteps  | 469      |
----------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 443      |
|    ep_rew_mean      | 853      |
|    exploration_rate | 0.995    |
| time/               |          |
|    episodes         | 24       |
|    fps              | 250      |
|    time_elapsed     | 2        |
|    total_timesteps  | 576      |
----------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 435      |
|    ep_rew_m

MoviePy - Done !
MoviePy - video ready /home/ec2-user/SageMaker/videos/xk82qzec/rl-video-step-50000-to-step-50400.mp4
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 380      |
|    ep_rew_mean      | 610      |
|    exploration_rate | 0.521    |
| time/               |          |
|    episodes         | 2372     |
|    fps              | 206      |
|    time_elapsed     | 244      |
|    total_timesteps  | 50401    |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 0.434    |
|    n_updates        | 10100    |
----------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 380      |
|    ep_rew_mean      | 609      |
|    exploration_rate | 0.52     |
| time/               |          |
|    episodes         | 2376     |
|    fps              | 206      |
|    time_elapsed     | 245      |
|    total_timesteps  | 50482    |
| train

MoviePy - Done !
MoviePy - video ready /home/ec2-user/SageMaker/videos/xk82qzec/rl-video-step-100000-to-step-100400.mp4
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 499      |
|    ep_rew_mean      | 1e+03    |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 4492     |
|    fps              | 194      |
|    time_elapsed     | 517      |
|    total_timesteps  | 100457   |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 2.85     |
|    n_updates        | 22614    |
----------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 499      |
|    ep_rew_mean      | 1e+03    |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 4496     |
|    fps              | 194      |
|    time_elapsed     | 517      |
|    total_timesteps  | 100588   |
| tra

...

MoviePy - Done !
MoviePy - video ready /home/ec2-user/SageMaker/videos/xk82qzec/rl-video-step-950000-to-step-950400.mp4
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 535      |
|    ep_rew_mean      | 905      |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 38296    |
|    fps              | 181      |
|    time_elapsed     | 5246     |
|    total_timesteps  | 950450   |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 3.69     |
|    n_updates        | 235112   |
----------------------------------
----------------------------------
| rollout/            |          |
|    ep_len_mean      | 534      |
|    ep_rew_mean      | 901      |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 38300    |
|    fps              | 181      |
|    time_elapsed     | 5246     |
|    total_timesteps  | 950552   |
| tra

MoviePy - Building video /home/ec2-user/SageMaker/videos/xk82qzec/rl-video-step-1000000-to-step-1000400.mp4.
MoviePy - Writing video /home/ec2-user/SageMaker/videos/xk82qzec/rl-video-step-1000000-to-step-1000400.mp4



MoviePy - Done !
MoviePy - video ready /home/ec2-user/SageMaker/videos/xk82qzec/rl-video-step-1000000-to-step-1000400.mp4


Saving video to /home/ec2-user/SageMaker/videos/xk82qzec/rl-video-step-1000000-to-step-1000400.mp4
MoviePy - Building video /home/ec2-user/SageMaker/videos/xk82qzec/rl-video-step-1000000-to-step-1000400.mp4.
MoviePy - Writing video /home/ec2-user/SageMaker/videos/xk82qzec/rl-video-step-1000000-to-step-1000400.mp4



MoviePy - Done !
MoviePy - video ready /home/ec2-user/SageMaker/videos/xk82qzec/rl-video-step-1000000-to-step-1000400.mp4
Mean reward: 1162.0 +/- 212.82856951076846


In [ ]:
import matplotlib.pyplot as plt
from IPython.display import display, clear_output
import time

# Load model
model = DQN.load("dqn_riverraid")

# Create renderable env
env = gym.make("ALE/Riverraid-v5", render_mode="rgb_array")
env = AtariWrapper(env)

obs, info = env.reset()
done = False

for _ in range(1000):
    action, _ = model.predict(obs, deterministic=True)
    obs, reward, done, truncated, info = env.step(action)

    # Render frame
    frame = env.render()
    plt.imshow(frame)
    plt.axis("off")
    clear_output(wait=True)
    display(plt.gcf())
    time.sleep(0.03)

    if done or truncated:
        obs, info = env.reset()

env.close()

In [ ]:
# should be changed to record a video, instead.